# Análise de Chamados da Cidade de Nova York
🎯 Objetivo do Projeto

Este projeto tem como foco analisar os chamados registrados na plataforma 311 da cidade de Nova York no ano de 2024, utilizando Databricks, PySpark e SQL para processar e transformar os dados. O intuito é construir um pipeline de dados estruturado nas camadas Bronze, Silver e Gold, permitindo avaliar a eficiência dos atendimentos por agência.

A partir da análise, buscamos responder questões como:

1️⃣ Quais são as agências com maior tempo médio de execução?

2️⃣ Qual a proporção de chamados fechados em relação ao total?

3️⃣ Qual a variação do tempo de execução dentro de cada agência?

🔗 Metodologia e Camadas de Dados
Para garantir integridade, qualidade e performance, seguimos uma arquitetura de Data Lakehouse, organizada em três camadas:

Bronze 🟤: Armazena os dados brutos sem transformações.

Silver ⚪: Processa e padroniza os dados, tratando inconsistências e garantindo qualidade.

Gold 🟡: Realiza transformações finais e estrutura os dados em um modelo otimizado para análise.

🛠 Ferramentas e Tecnologias Utilizadas

Databricks (ambiente de processamento de dados)

PySpark (manipulação de grandes volumes de dados)

SQL (consultas e modelagem dos dados)

### Passo 1: Bronze – Carregar os Dados Brutos

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import to_timestamp, col, unix_timestamp, expr, date_format, concat, lit, floor, when, count, lpad, concat_ws
from pyspark.sql.types import TimestampType


In [0]:

# Criando a sessão Spark
spark = SparkSession.builder.getOrCreate()

# Definindo os caminhos no DBFS
file_chamados = "dbfs:/FileStore/Service_Requests_2024.csv"
file_status = "dbfs:/FileStore/Closed_Requests_2024.csv"
file_agencias = "dbfs:/FileStore/Agency_Requests_2024.csv"

# Função para carregar CSV do DBFS para um DataFrame Spark
def load_csv_to_spark(file_path):
    df_spark = spark.read.csv(file_path, header=True, inferSchema=True)
    return df_spark

# Carregando os DataFrames
df_chamados = load_csv_to_spark(file_chamados)
df_status = load_csv_to_spark(file_status)
df_agencias = load_csv_to_spark(file_agencias)

# Criando Views Temporárias para consultas SQL
df_chamados.createOrReplaceTempView("df_chamados")
df_status.createOrReplaceTempView("df_status")
df_agencias.createOrReplaceTempView("df_agencias")



In [0]:
%sql
SELECT * FROM df_chamados LIMIT 5;


Unique Key Created Date Closed Date Agency Complaint Type Descriptor Location Type Incident Zip Incident Address Street Name City Community Board BBL Borough 59895660 01/01/2024 03:39:34 PM 01/01/2024 05:05:51 PM NYPD Illegal Parking Unauthorized Bus Layover Street/Sidewalk 11201 FRONT STREET FRONT STREET null 02 BROOKLYN null BROOKLYN 59895699 01/01/2024 03:40:27 PM 01/02/2024 01:01:55 AM NYPD Illegal Parking Blocked Hydrant Street/Sidewalk 11102 30-54 33 STREET 33 STREET ASTORIA 01 QUEENS 4006160056 QUEENS 59898622 01/01/2024 03:40:39 PM 01/01/2024 04:14:31 PM NYPD Noise - Street/Sidewalk Loud Music/Party Street/Sidewalk 11218 OCEAN PARKWAY OCEAN PARKWAY null Unspecified BROOKLYN null BROOKLYN 59896001 01/01/2024 03:40:41 PM 01/01/2024 05:23:45 PM NYPD Noise - Residential Loud Music/Party Residential Building/House 11419 101-54 109 STREET 109 STREET SOUTH RICHMOND HILL 09 QUEENS 4094260029 QUEENS 59894896 01/01/2024 03:40:52 PM 01/01/2024 05:04:14 PM NYPD Illegal Parking Posted Parking Sign Violation Street/Sidewalk 11201 46 OLD FULTON STREET OLD FULTON STREET BROOKLYN 02 BROOKLYN 3002020012 BROOKLYN

In [0]:
%sql
SELECT * FROM df_status LIMIT 5;


Unique Key Status Due Date Resolution Description Resolution Action Updated Date 59895660 Closed null The Police Department responded and upon arrival those responsible for the condition were gone. 01/01/2024 05:05:54 PM 59895699 Closed null The Police Department responded and upon arrival those responsible for the condition were gone. 01/02/2024 01:01:58 AM 59898622 Closed null The Police Department responded to the complaint and took action to fix the condition. 01/01/2024 04:14:33 PM 59896001 Closed null The Police Department responded to the complaint and with the information available observed no evidence of the violation at that time. 01/01/2024 05:23:50 PM 59894896 Closed null The Police Department responded to the complaint and took action to fix the condition. 01/01/2024 05:04:17 PM

In [0]:
%sql
SELECT * FROM df_agencias LIMIT 5;

Agency Agency Name NYPD New York City Police Department DEP Department of Environmental Protection HPD Department of Housing Preservation and Development DOT Department of Transportation DSNY Department of Sanitation

###Passo 2: Silver – Transformação dos Dados e Junção das Tabelas

01 Renomear colunas para manter um padrão

02 Corrigir tipos de dados (se necessário)

03 Criar colunas derivadas (se fizer sentido)

03 Unir os DataFrames em um único DataFrame df_silver

In [0]:
# Renomeando colunas para remover espaços
columns_map = {
    "Unique Key": "Unique_Key",
    "Created Date": "Created_Date",
    "Closed Date": "Closed_Date",
    "Complaint Type": "Complaint_Type",
    "Resolution Description": "Resolution_Description",
    "Resolution Action Updated Date": "Resolution_Action_Updated_Date",
    "Agency Name": "Agency_Name",
    "Due Date": "Due_Date",
}

df_chamados = df_chamados.select([col(c).alias(columns_map.get(c, c)) for c in df_chamados.columns])
df_status = df_status.select([col(c).alias(columns_map.get(c, c)) for c in df_status.columns])
df_agencias = df_agencias.select([col(c).alias(columns_map.get(c, c)) for c in df_agencias.columns])

# Realizando as junções
df_silver = df_chamados.join(df_status, on="Unique_Key", how="left")
df_silver = df_silver.join(df_agencias, on="Agency", how="left")

# Atualizando a View Temporária
df_silver.createOrReplaceTempView("df_silver")


In [0]:
%sql
Select * from df_silver limit 5;

Agency Unique_Key Created_Date Closed_Date Complaint_Type Descriptor Location Type Incident Zip Incident Address Street Name City Community Board BBL Borough Status Due_Date Resolution_Description Resolution_Action_Updated_Date Agency_Name HPD 60363774 02/19/2024 11:39:26 AM 02/21/2024 09:11:10 PM HEAT/HOT WATER ENTIRE BUILDING RESIDENTIAL BUILDING 10452 15 CLARKE PLACE EAST CLARKE PLACE EAST BRONX 04 BRONX 2028400038 BRONX Closed null The complaint you filed is a duplicate of a condition already reported by another tenant for a building-wide condition. The original complaint is still open. HPD may attempt to contact you to verify the correction of the condition or may conduct an inspection of your unit if the original complainant is not available for verification. 02/21/2024 12:00:00 AM Department of Housing Preservation and Development HPD 60365751 02/19/2024 11:39:24 AM 02/21/2024 08:28:16 PM HEAT/HOT WATER APARTMENT ONLY RESIDENTIAL BUILDING 10003 81 EAST 10 STREET EAST 10 STREET NEW YORK 03 MANHATTAN 1005560015 MANHATTAN Closed null The Department of Housing Preservation and Development responded to a complaint of no heat or hot water and was advised by a tenant in the building that heat and hot water had been restored. If the condition still exists, please file a new complaint. 02/21/2024 12:00:00 AM Department of Housing Preservation and Development HPD 60365847 02/19/2024 11:39:23 AM 02/21/2024 08:03:50 PM HEAT/HOT WATER ENTIRE BUILDING RESIDENTIAL BUILDING 10025 107 WEST 109 STREET WEST 109 STREET NEW YORK 07 MANHATTAN 1018640023 MANHATTAN Closed null The Department of Housing Preservation and Development was not able to gain access to your apartment or others in the building to inspect for a lack of heat or hot water. The complaint has been closed. If the condition still exists, please file a new complaint. 02/21/2024 12:00:00 AM Department of Housing Preservation and Development NYPD 61288137 05/28/2024 08:20:02 AM 05/28/2024 09:13:58 AM Encampment N/A Residential Building/House 10018 522 WEST 37 STREET WEST 37 STREET NEW YORK 04 MANHATTAN 1007080048 MANHATTAN Closed null The Police Department visited the location and has referred the complaint to the Department of Homeless Services (DHS) for further action. DHS will inspect the condition and update your Service Request with more information. 05/28/2024 09:14:39 AM New York City Police Department NYPD 61761803 07/10/2024 05:38:03 AM 07/10/2024 07:57:38 AM Illegal Parking Posted Parking Sign Violation Street/Sidewalk 11357 150-164 POWELLS COVE BOULEVARD POWELLS COVE BOULEVARD WHITESTONE 07 QUEENS 4045190036 QUEENS Closed null The Police Department responded to the complaint and determined that police action was not necessary. 07/10/2024 07:57:41 AM New York City Police Department

In [0]:
# Convertendo colunas de data para Timestamp
df_silver = df_silver.withColumn("Created_Date", date_format(to_timestamp("Created_Date", "MM/dd/yyyy hh:mm:ss a"), "yyyy-MM-dd HH:mm:ss"))
df_silver = df_silver.withColumn("Closed_Date", date_format(to_timestamp("Closed_Date", "MM/dd/yyyy hh:mm:ss a"), "yyyy-MM-dd HH:mm:ss"))
df_silver = df_silver.withColumn("Resolution_Action_Updated_Date", date_format(to_timestamp("Resolution_Action_Updated_Date", "MM/dd/yyyy hh:mm:ss a"), "yyyy-MM-dd HH:mm:ss"))
df_silver = df_silver.withColumn("Due_Date", date_format(to_timestamp("Due_Date", "MM/dd/yyyy hh:mm:ss a"), "yyyy-MM-dd HH:mm:ss"))

#df_silver = df_silver.withColumn("Created_Date", to_timestamp("Created_Date", "MM/dd/yyyy hh:mm:ss a"))
#df_silver = df_silver.withColumn("Closed_Date", to_timestamp("Closed_Date", "MM/dd/yyyy hh:mm:ss a"))


# Atualizando a View Temporária
df_silver.createOrReplaceTempView("df_silver")


In [0]:
%sql
SELECT Unique_key, Created_Date, Closed_Date, status, Resolution_Action_Updated_Date, Due_Date FROM df_silver;

Unique_key Created_Date Closed_Date status Resolution_Action_Updated_Date Due_Date 59893986 2024-01-01 16:11:00 2024-01-01 18:00:00 Closed 2024-01-01 18:00:00 null 59894010 2024-01-01 15:42:04 2024-01-01 17:39:46 Closed 2024-01-01 17:39:50 null 59894030 2024-01-01 17:20:32 2024-01-01 18:30:10 Closed 2024-01-01 18:30:12 null 59894037 2024-01-01 21:37:28 2024-01-01 22:06:38 Closed 2024-01-01 22:06:42 null 59894039 2024-01-01 16:18:39 2024-01-01 17:32:53 Closed 2024-01-01 17:32:56 null 59894047 2024-01-01 23:51:23 2024-01-02 00:56:33 Closed 2024-01-02 00:56:38 null 59894062 2024-01-01 16:45:18 2024-01-01 17:40:10 Closed 2024-01-01 17:40:15 null 59894072 2024-01-02 00:38:03 2024-01-02 00:54:49 Closed 2024-01-02 00:54:53 null 59894084 2024-01-02 00:27:41 2024-01-02 00:41:02 Closed 2024-01-02 00:41:06 null 59894137 2024-01-01 17:08:28 2024-01-01 19:19:07 Closed 2024-01-01 19:19:11 null 59894142 2024-01-01 23:54:09 2024-01-02 00:31:51 Closed 2024-01-02 00:31:58 null 59894144 2024-01-01 20:19:51 2024-01-01 22:36:57 Closed 2024-01-01 22:37:01 null 59894163 2024-01-01 22:29:07 2024-01-01 22:36:58 Closed 2024-01-01 22:37:02 null 59894177 2024-01-01 19:48:14 2024-01-01 20:19:17 Closed 2024-01-01 20:19:20 null 59894181 2024-01-01 18:39:33 2024-01-01 19:12:31 Closed 2024-01-01 19:12:33 null 59894182 2024-01-01 16:43:55 2024-01-01 20:13:06 Closed 2024-01-01 20:13:10 null 59894204 2024-01-01 22:55:15 2024-01-01 23:22:34 Closed 2024-01-01 23:22:37 null 59894229 2024-01-01 21:03:42 2024-01-01 22:02:09 Closed 2024-01-01 22:02:12 null 59894255 2024-01-01 23:02:05 2024-01-01 23:11:57 Closed 2024-01-01 23:12:01 null 59894301 2024-01-01 22:38:52 2024-01-01 22:49:57 Closed 2024-01-01 22:50:01 null 59894368 2024-01-01 17:12:09 2024-01-01 17:40:42 Closed 2024-01-01 17:40:46 null 59894386 2024-01-01 23:13:59 2024-01-01 23:18:35 Closed 2024-01-01 23:18:42 null 59894414 2024-01-01 23:57:43 2024-01-03 20:15:19 Closed 2024-01-03 00:00:00 null 59894440 2024-01-01 16:09:00 2024-01-02 07:08:47 Closed 2024-01-02 00:00:00 null 59894453 2024-01-01 17:53:53 2024-01-02 21:06:15 Closed 2024-01-02 00:00:00 null 59894454 2024-01-01 19:46:30 2024-01-02 19:48:53 Closed 2024-01-02 00:00:00 null 59894456 2024-01-01 19:40:31 2024-01-02 16:18:50 Closed 2024-01-02 00:00:00 null 59894471 2024-01-01 20:24:52 2024-01-02 16:07:35 Closed 2024-01-02 00:00:00 null 59894480 2024-01-01 16:18:39 2024-01-01 17:27:37 Closed 2024-01-01 00:00:00 null 59894494 2024-01-01 17:40:56 2024-01-02 11:10:35 Closed 2024-01-02 00:00:00 null 59894520 2024-01-01 23:38:59 2024-02-02 07:25:52 Closed 2024-02-02 00:00:00 null 59894528 2024-01-01 16:35:25 2024-01-18 07:20:57 Closed 2024-01-18 00:00:00 null 59894556 2024-01-01 22:23:02 2024-01-02 13:59:39 Closed 2024-01-02 00:00:00 null 59894576 2024-01-01 19:50:07 2024-01-01 19:51:36 Closed 2024-01-01 19:51:39 null 59894605 2024-01-01 21:36:20 2024-01-02 02:21:44 Closed 2024-01-02 02:21:50 null 59894626 2024-01-01 19:45:24 2024-01-23 11:32:36 Closed 2024-01-23 11:32:42 null 59894642 2024-01-01 20:54:07 2024-01-02 01:51:24 Closed 2024-01-02 01:51:29 null 59894643 2024-01-02 00:51:53 2024-01-02 01:29:33 Closed 2024-01-02 01:29:39 null 59894654 2024-01-01 16:34:34 2024-01-19 14:21:06 Closed 2024-01-19 14:21:11 null 59894657 2024-01-01 16:23:37 2024-01-19 14:20:58 Closed 2024-01-19 14:21:03 null 59894664 2024-01-02 01:17:31 2024-01-02 02:54:05 Closed 2024-01-02 02:54:09 null 59894665 2024-01-01 23:26:47 2024-01-02 02:06:09 Closed 2024-01-02 02:06:13 null 59894677 2024-01-01 20:12:00 2024-01-02 09:46:00 Closed 2024-01-02 12:00:00 null 59894714 2024-01-01 16:59:24 2024-01-02 22:16:55 Closed 2024-01-02 22:16:59 null 59894719 2024-01-01 15:59:50 2024-01-05 07:01:35 Closed 2024-01-05 07:01:35 null 59894748 2024-01-01 17:58:20 2024-01-02 16:57:26 Closed 2024-01-02 16:57:31 null 59894814 2024-01-01 19:23:47 2024-01-01 22:37:37 Closed 2024-01-01 22:37:46 null 59894845 2024-01-01 20:51:43 2024-01-01 21:17:28 Closed 2024-01-01 21:17:32 null 59894882 2024-01-01 23:33:51 

#### Tabela chamados

In [0]:
%sql
SELECT COUNT(*) AS Nulos_Closed_Date
FROM df_silver
WHERE Closed_Date IS NULL AND Status = 'Closed'

Nulos_Closed_Date 27561

In [0]:
%sql
SELECT Unique_Key, Closed_Date, Resolution_Action_Updated_Date
FROM df_silver
WHERE Closed_Date IS NULL AND Status = 'Closed'

Unique_Key Closed_Date Resolution_Action_Updated_Date 59957409 null 2024-01-07 18:34:32 59999568 null 2024-01-15 20:10:56 60099599 null 2024-01-21 11:05:15 60099596 null 2024-01-21 19:06:20 60151665 null 2024-01-26 19:55:15 60161104 null 2024-01-27 10:52:06 60154977 null 2024-01-27 20:29:02 60164671 null 2024-01-28 15:54:35 60207003 null 2024-02-05 12:39:17 60231396 null 2024-02-07 04:57:48 59918815 null 2024-01-03 16:36:13 59972066 null 2024-01-12 04:10:06 59980079 null 2024-01-10 11:25:25 60141278 null 2024-01-25 12:04:26 60242730 null 2024-02-09 01:36:07 60247933 null 2024-02-06 14:00:40 60296102 null 2024-02-13 04:52:29 59903307 null 2024-01-02 16:31:14 59968114 null 2024-01-09 05:00:24 60026420 null 2024-01-14 15:42:43 60051442 null 2024-01-18 03:32:54 60087657 null 2024-01-20 09:29:55 60141266 null 2024-01-25 11:35:31 60185818 null 2024-02-02 00:48:07 60251846 null 2024-02-11 23:13:44 60251845 null 2024-02-06 11:25:49 60313038 null 2024-02-14 01:10:46 60311745 null 2024-02-14 11:23:00 59980080 null 2024-01-10 18:22:11 60041383 null 2024-01-17 01:02:15 60322603 null 2024-02-16 02:04:35 59981549 null 2024-01-18 21:56:10 60016427 null 2024-01-14 07:47:33 60059191 null 2024-01-18 11:27:03 60098477 null 2024-01-21 11:39:18 60204278 null 2024-02-04 08:57:35 60291256 null 2024-02-10 05:02:54 59975999 null 2024-01-09 14:10:18 59990499 null 2024-01-11 05:04:04 60044158 null 2024-01-20 07:49:40 60154019 null 2024-01-27 21:53:07 60268453 null 2024-02-08 17:32:08 60279182 null 2024-02-09 20:17:37 59901983 null 2024-01-03 02:52:02 59913612 null 2024-01-03 11:49:57 59998323 null 2024-01-15 07:34:43 60006884 null 2024-01-12 19:30:51 60014413 null 2024-01-14 09:47:42 60034690 null 2024-01-15 17:28:16 60061009 null 2024-01-18 15:29:01 60123548 null 2024-01-25 12:18:10 60163796 null 2024-01-28 11:22:13 60240100 null 2024-02-06 07:22:35 60293298 null 2024-02-12 05:08:07 59965377 null 2024-01-09 04:58:12 59968109 null 2024-01-08 19:35:27 60011492 null 2024-01-14 10:49:14 60082316 null 2024-01-20 16:42:16 60085664 null 2024-01-24 20:09:48 60124800 null 2024-01-30 00:13:37 60220238 null 2024-02-04 11:53:40 60294235 null 2024-02-11 20:02:20 60332882 null 2024-02-16 02:05:02 59926798 null 2024-01-05 16:19:56 59959932 null 2024-01-08 20:09:22 60096149 null 2024-01-21 14:56:16 60162002 null 2024-01-28 10:56:02 60264780 null 2024-02-08 07:42:16 60283854 null 2024-02-09 12:02:53 60283852 null 2024-02-09 19:52:58 60309172 null 2024-02-14 18:03:55 59932091 null 2024-01-04 19:27:13 60059187 null 2024-01-18 06:27:56 60064615 null 2024-01-23 11:45:40 60093870 null 2024-01-21 16:47:31 60148990 null 2024-01-26 18:42:50 60278079 null 2024-02-11 09:05:58 60297970 null 2024-02-11 16:01:55 59904598 null 2024-01-03 08:59:26 59968087 null 2024-01-08 18:27:11 59973388 null 2024-01-09 18:26:51 59974644 null 2024-01-09 18:54:13 60146496 null 2024-01-27 00:35:09 60166582 null 2024-02-08 08:22:19 60204283 null 2024-02-03 08:39:11 60224135 null 2024-02-05 08:13:08 60222193 null 2024-02-03 16:59:00 60237573 null 2024-02-05 19:49:25 60315589 null 2024-02-13 11:21:03 59966721 null 2024-01-13 07:17:20 59966718 null 2024-01-08 23:47:52 59981541 null 2024-01-10 13:19:35 59990497 null 2024-01-17 18:07:07 60084646 null 2024-01-20 11:53:51 60102063 null 2024-01-22 18:40:41 60176332 null 2024-01-29 11:32:58 60283857 null 2024-02-13 08:21:29 59917491 null 2024-01-06 09:32:27 59964043 null 2024-01-12 17:25:31 59958658 null 2024-01-11 04:19:32 60062765 null 2024-01-18 12:21:55 60148997 null 2024-01-30 19:45:08 60158059 null 2024-01-27 08:38:10 59903311 null 2024-01-02 15:09:31 59958654 null 2024-01-10 10:56:26 59970753 null 2024-01-11 05:06:45 59976006 null 2024-01-15 07:43:54 59978628 null 2024-01-09 19:00:17 60235019 null 2024-02-05 03:21:00 60299797 null 2024-02-16 09:06:45 60352172 null 2024-02-18 09:44:52 59918825 null 2024-01-04 09:36:00 59926799 null 2024-01-05 17:56:54 59952556 null 2024-01-07 18:14:22 60207005 null 2024-02-02 03:08:53 60266037 null 2024-02-07 22:04:43 60

In [0]:
#Considerando que há 27.561 linhas com valores ausentes, o problema será solucionado substituindo os valores nulos da coluna 'Closed_Date' pela data presente na coluna 'Resolution_Action_Updated_Date"

from pyspark.sql.functions import when, col

df_silver = df_silver.withColumn(
    "Closed_Date",
    when((col("Closed_Date").isNull()) & (col("Status") == "Closed"), col("Resolution_Action_Updated_Date"))
    .otherwise(col("Closed_Date"))
)

# Atualizando a View Temporária
df_silver.createOrReplaceTempView("df_silver")


In [0]:
%sql
SELECT Unique_key, Closed_Date
FROM df_silver
WHERE Closed_Date IS NULL AND Status = 'Closed'

Unique_key Closed_Date 60872924 null

In [0]:
# Mesmo após a substituição realizada, foi gerado apenas um dado nulo. Este será excluído do banco a fim de preservar a qualidade dos dados, considerando que se trata de um caso isolado e que não causará impacto significativo

df_silver = df_silver.filter(col("Unique_Key") != 60872924)

# Atualizando a View Temporária
df_silver.createOrReplaceTempView("df_silver")


In [0]:
%sql
SELECT Unique_key, Closed_Date
FROM df_silver
WHERE Closed_Date IS NULL AND Status = 'Closed'

Unique_key Closed_Date

#### Tabela `Status`

In [0]:
%sql
SELECT Unique_Key, Status 
FROM df_silver
WHERE Status IS NULL

Unique_Key Status

#### Tabela Agencias

In [0]:
%sql
SELECT Unique_Key, Agency, Agency_Name
FROM df_silver
WHERE Agency IS NULL OR Agency_Name IS NULL


Unique_Key Agency Agency_Name 61332341 3-1-1 null

In [0]:
# Este será excluído do banco a fim de preservar a qualidade dos dados, considerando que se trata de um caso isolado e que não causará impacto significativo

df_silver = df_silver.filter(col("Unique_Key") != 61332341)

# Atualizando a View Temporária
df_silver.createOrReplaceTempView("df_silver")

In [0]:
# Garantindo que as colunas de data estejam no formato timestamp
df_silver = df_silver.withColumn("Created_Date", to_timestamp(col("Created_Date"), "yyyy-MM-dd HH:mm:ss"))
df_silver = df_silver.withColumn("Closed_Date", to_timestamp(col("Closed_Date"), "yyyy-MM-dd HH:mm:ss"))
df_silver = df_silver.withColumn("Resolution_Action_Updated_Date", to_timestamp(col("Resolution_Action_Updated_Date"), "yyyy-MM-dd HH:mm:ss"))

# Calculando a diferença total em segundos
df_silver = df_silver.withColumn("Execution_Time_Seconds", unix_timestamp(col("Closed_Date")) - unix_timestamp(col("Created_Date")))

# Garantindo que não há valores negativos
df_silver = df_silver.withColumn("Execution_Time_Seconds", when(col("Execution_Time_Seconds") < 0, 0).otherwise(col("Execution_Time_Seconds")))

# Convertendo para horas, minutos e segundos corretamente (sem truncamento)
df_silver = df_silver.withColumn("Execution_Hours", (col("Execution_Time_Seconds") / 3600).cast("int"))  # Sem limite de 99h
df_silver = df_silver.withColumn("Execution_Minutes", floor((col("Execution_Time_Seconds") % 3600) / 60))
df_silver = df_silver.withColumn("Execution_Seconds", (col("Execution_Time_Seconds") % 60).cast("int"))

# Formatando no padrão HH:MM:SS com dois dígitos (inclui valores acima de 99 horas)
df_silver = df_silver.withColumn(
    "Execution_Time",
    concat_ws(":",
        col("Execution_Hours").cast("string"),  # Mantém acima de 99h sem truncar
        lpad(col("Execution_Minutes").cast("string"), 2, "0"),
        lpad(col("Execution_Seconds").cast("string"), 2, "0")
    )
)

# Removendo colunas auxiliares
# df_silver = df_silver.drop("Execution_Time_Seconds", "Execution_Hours", "Execution_Minutes", "Execution_Seconds")

# Atualizando a View Temporária
df_silver.createOrReplaceTempView("df_silver")


In [0]:
colunas_para_remover = ["Complaint_Type", "Street Name", "City", "Location Type","Incident Zip","Incident Address","Street Name,City","Community Board","BBL", "Borough", "Due_Date"]  # Exemplo de colunas
df_gold = df_silver.drop(*colunas_para_remover)

# Atualizando a View Temporária
df_gold.createOrReplaceTempView("df_gold")

In [0]:
%sql
SELECT * FROM df_gold LIMIT 10;

Agency Unique_Key Created_Date Closed_Date Descriptor Status Resolution_Description Resolution_Action_Updated_Date Agency_Name Execution_Time_Seconds Execution_Hours Execution_Minutes Execution_Seconds Execution_Time DEP 59893986 2024-01-01T16:11:00.000+0000 2024-01-01T18:00:00.000+0000 Catch Basin Clogged/Flooding (Use Comments) (SC) Closed The Department of Environment Protection inspected your complaint but could not find the problem you reported. If the condition persists, please call 311 (or 212-639-9675 if calling from a non-New York City area code) with more detailed information to submit a new complaint. 2024-01-01T18:00:00.000+0000 Department of Environmental Protection 6540 1 49 0 1:49:00 NYPD 59894010 2024-01-01T15:42:04.000+0000 2024-01-01T17:39:46.000+0000 Blocked Hydrant Closed The Police Department responded and upon arrival those responsible for the condition were gone. 2024-01-01T17:39:50.000+0000 New York City Police Department 7062 1 57 42 1:57:42 NYPD 59894030 2024-01-01T17:20:32.000+0000 2024-01-01T18:30:10.000+0000 Blocked Hydrant Closed The Police Department issued a summons in response to the complaint. 2024-01-01T18:30:12.000+0000 New York City Police Department 4178 1 9 38 1:09:38 NYPD 59894037 2024-01-01T21:37:28.000+0000 2024-01-01T22:06:38.000+0000 Blocked Hydrant Closed The Police Department responded and upon arrival those responsible for the condition were gone. 2024-01-01T22:06:42.000+0000 New York City Police Department 1750 0 29 10 0:29:10 NYPD 59894039 2024-01-01T16:18:39.000+0000 2024-01-01T17:32:53.000+0000 Blocked Hydrant Closed The Police Department responded and upon arrival those responsible for the condition were gone. 2024-01-01T17:32:56.000+0000 New York City Police Department 4454 1 14 14 1:14:14 NYPD 59894047 2024-01-01T23:51:23.000+0000 2024-01-02T00:56:33.000+0000 Blocked Sidewalk Closed The Police Department responded to the complaint and took action to fix the condition. 2024-01-02T00:56:38.000+0000 New York City Police Department 3910 1 5 10 1:05:10 NYPD 59894062 2024-01-01T16:45:18.000+0000 2024-01-01T17:40:10.000+0000 Commercial Overnight Parking Closed The Police Department responded to the complaint and determined that police action was not necessary. 2024-01-01T17:40:15.000+0000 New York City Police Department 3292 0 54 52 0:54:52 NYPD 59894072 2024-01-02T00:38:03.000+0000 2024-01-02T00:54:49.000+0000 Posted Parking Sign Violation Closed The Police Department responded to the complaint and determined that police action was not necessary. 2024-01-02T00:54:53.000+0000 New York City Police Department 1006 0 16 46 0:16:46 NYPD 59894084 2024-01-02T00:27:41.000+0000 2024-01-02T00:41:02.000+0000 Posted Parking Sign Violation Closed The Police Department responded to the complaint and determined that police action was not necessary. 2024-01-02T00:41:06.000+0000 New York City Police Department 801 0 13 21 0:13:21 NYPD 59894137 2024-01-01T17:08:28.000+0000 2024-01-01T19:19:07.000+0000 No Access Closed The Police Department responded to the complaint and with the information available observed no evidence of the violation at that time. 2024-01-01T19:19:11.000+0000 New York City Police Department 7839 2 10 39 2:10:39

### Passo 3: Gold - Transformações finais e construção do esquema estrela

####Catálogo de Dados - Esquema Estrela

---

#### Tabela Fato: `Fato_Unique_Keys`

| Coluna                        | Tipo                 | Chave       | Descrição                                      |
|--------------------------------|----------------------|------------|------------------------------------------------|
| ID_Unique_Key                | INT                  | PK         | Identificador único do Unique_Key            |
| ID_Agencia                    | STRING               | FK → `Dim_Agencia` | Identificador da agência responsável |
| ID_Data                       | STRING               | FK → `Dim_Tempo`   | Identificador da data do chamado       |
| Created_Date                  | DATETIME             | -          | Data de criação do chamado                    |
| Closed_Date                   | DATETIME             | -          | Data de fechamento do chamado                 |
| Descriptor                     | STRING               | -          | Tipo ou descrição da solicitação              |
| Status                         | STRING               | -          | Status do chamado                            |
| Resolution_Description         | STRING               | -          | Descrição da resolução aplicada               |
| Resolution_Action_Updated_Date | STRING               | -          | Data da última atualização da resolução       |
| Execution_Time                 | STRING               | -          | Tempo total de execução do Unique_Key        |

---

#### Tabela Dimensão: `Dim_Agencia`

| Coluna                      | Tipo                 | Chave | Descrição                                     |
|-----------------------------|----------------------|-------|-----------------------------------------------|
| ID_Agencia                  | STRING               | PK    | Identificador único da agência               |
| Agency                      | STRING               | -     | Sigla da agência                             |
| Agency_Name                 | STRING               | -     | Nome completo da agência                     |

---

#### Tabela Dimensão: `Dim_Tempo`

| Coluna                      | Tipo                 | Chave | Descrição                                     |
|-----------------------------|----------------------|-------|-----------------------------------------------|
| ID_Data                     | STRING               | PK    | Identificador único da data (YYYYMMDD)       |
| Ano                         | INT                  | -     | Ano da data                                  |
| Mês                         | INT                  | -     | Mês da data                                  |
| Dia                         | INT                  | -     | Dia da data                                  |
| Dia_da_Semana               | STRING               | -     | Nome do dia da semana                        |

---

🔹 **Observação:**  
- **Chave primária (`PK`)**: `ID_Unique_Key` na tabela fato, `ID_Agencia` e `ID_Data` nas tabelas dimensão.  
- **Chave estrangeira (`FK`)**: `ID_Agencia` e `ID_Data` na tabela fato, ligando-se às tabelas dimensão.  
- **Colunas adicionadas**: `Created_Date`, `Closed_Date`, `Descriptor`, `Resolution_Description`, `Resolution_Action_Updated_Date`, e `Execution_Time` para manter a rastreabilidade.  



In [0]:
%sql
SELECT 
    Status, 
    COUNT(*) AS Total_Requests,
    ROUND(COUNT(*) * 100.0 / SUM(COUNT(*)) OVER (), 2) AS Percentage
FROM df_gold
GROUP BY Status
ORDER BY Percentage DESC;


Status Total_Requests Percentage Closed 3353582 97.23 In Progress 61001 1.77 Open 18196 0.53 Assigned 11426 0.33 Pending 3679 0.11 Started 966 0.03 Unspecified 102 0.00

In [0]:
%sql
SELECT 
    Agency, 
    COUNT(*) AS Total_Closed_Calls
FROM df_gold
WHERE Status = 'Closed'
GROUP BY Agency
ORDER BY Total_Closed_Calls DESC
LIMIT 10;


Agency Total_Closed_Calls NYPD 1541454 HPD 721639 DSNY 303990 DOT 196962 DEP 188771 DPR 96656 DOB 90921 DOHMH 86044 DHS 51894 TLC 33109

In [0]:
%sql
SELECT 
    Agency, 
    Agency_Name, 
    ROUND(AVG(Execution_Time_Seconds) / 3600, 2) AS Avg_Execution_Time_Hours
FROM df_gold
WHERE Status = 'Closed'
GROUP BY Agency, Agency_Name
ORDER BY Avg_Execution_Time_Hours DESC
LIMIT 10;


Agency Agency_Name Avg_Execution_Time_Hours TLC Taxi and Limousine Commission 1722.98 DOE Department of Education 1297.03 DOHMH Department of Health and Mental Hygiene 1187.36 DPR Department of Parks and Recreation 1101.92 DOB Department of Buildings 921.59 EDC Economic Development Corporation 812.64 DCWP Department of Consumer and Worker Protection 376.17 OTI Office of Technology and Innovation 307.39 HPD Department of Housing Preservation and Development 297.7 DOT Department of Transportation 207.78

In [0]:
%sql
SELECT 
    Agency, 
    Agency_Name, 
    ROUND(MIN(Execution_Time_Seconds) / 3600, 2) AS Min_Execution_Time_Hours, 
    ROUND(MAX(Execution_Time_Seconds) / 3600, 2) AS Max_Execution_Time_Hours
FROM df_gold
WHERE Status = 'Closed'
GROUP BY Agency, Agency_Name
ORDER BY Max_Execution_Time_Hours DESC
LIMIT 10;


Agency Agency_Name Min_Execution_Time_Hours Max_Execution_Time_Hours DOB Department of Buildings 0.0 10783.74 DOT Department of Transportation 0.0 10747.88 DPR Department of Parks and Recreation 0.0 10709.22 HPD Department of Housing Preservation and Development 0.0 9714.16 DEP Department of Environmental Protection 0.0 9625.32 DSNY Department of Sanitation 0.0 9511.94 TLC Taxi and Limousine Commission 0.0 9167.62 DOHMH Department of Health and Mental Hygiene 0.0 9010.57 DCWP Department of Consumer and Worker Protection 2.03 8854.09 NYPD New York City Police Department 0.0 7584.94

##### Conclusões e Próximos Passos

🔍 Resultados Obtidos

Até o momento, conseguimos responder às seguintes questões:

1️⃣ Quais são as agências com maior tempo médio de execução?

* A TLC (Taxi and Limousine Commission) tem o maior tempo médio de execução, seguida pelo DOE (Department of Education) e DOHMH (Department of Health and Mental Hygiene). Chamados que levaram muitos dias para serem fechados, podem indicar burocratização ou ineficiência em algumas agências como chamados esquecidos ou fechados muito tempo depois que foi de fato executado.

* Algumas agências, como a NYPD, apresentam tempos médios muito baixos, indicando processos mais rápidos. Isso pode sugerir que a polícia resolve chamados de forma mais ágil em comparação com outras agências, ou que o tipo de chamado tratado por eles é diferente.

2️⃣ Qual a proporção de chamados Fechados?

* Calculamos o percentual de chamados concluídos em relação ao total, fornecendo um indicador da eficiência operacional do sistema. 

3️⃣ Qual a variação do tempo de execução dentro de cada agência?

* Identificamos o tempo mínimo e máximo de execução por agência, permitindo avaliar a consistência e possíveis gargalos nos processos internos.

💡 Conclusões e Próximos Passos

✅ O alto tempo médio de execução em algumas agências pode indicar gargalos operacionais, seja por falta de recursos ou processos burocráticos.

✅ A proporção de chamados fechados pode ser um bom indicador de eficiência operacional e deve ser acompanhada ao longo do tempo.

✅ A baixa variação no tempo de execução de algumas agências sugere que possuem fluxos bem padronizados e previsíveis. Porém também pode representar algum erro no dado como por exemplo, mal registrado.